In [ ]:
import pandas as pd
import numpy as np
from pprint import pprint

In [ ]:
# @title Setup
from google.colab import auth
from google.cloud import bigquery
from google.colab import data_table

project = 'centered-radius-89610' # Project ID inserted based on the query results selected to explore
location = 'EU' # Location inserted based on the query results selected to explore
client = bigquery.Client(project=project, location=location)
data_table.enable_dataframe_formatter()
auth.authenticate_user()

## Reference SQL syntax from the original job
Use the ```jobs.query```
[method](https://cloud.google.com/bigquery/docs/reference/rest/v2/jobs/query) to
return the SQL syntax from the job. This can be copied from the output cell
below to edit the query now or in the future. Alternatively, you can use
[this link](https://console.cloud.google.com/bigquery?j=centered-radius-89610:EU:bquxjob_341e6c0c_185cd6db6c2)
back to BigQuery to edit the query within the BigQuery user interface.

In [ ]:
# Running this code will display the query used to generate your previous job

job = client.get_job('bquxjob_341e6c0c_185cd6db6c2') # Job ID inserted based on the query results selected to explore
print(job.query)

with consolidated_events AS (
SELECT 
distinct 
    d.app_adjust_id,
    w.experiment_id,  -- A/B test name 
    CASE 
        WHEN w.variation_name = 'ctrl' THEN 'Control'
        WHEN w.variation_name = 'on' THEN 'Test'
        ELSE NULL 
        END AS test_assignment, 
     w.is_active,
    derived_tstamp,
    c.client_id,
    b.booking_id,
    os_family
FROM `snowplow-pipelines.rt_pipeline_prod1.consolidated_events` e 
LEFT JOIN UNNEST (e.com_goeuro_wasabi_context_1) w
LEFT JOIN UNNEST (e.com_goeuro_goeuro_tracking_ids_context_1) c
LEFT JOIN UNNEST (e.com_goeuro_system_versions_context_1) d
left join unnest (e.com_snowplowanalytics_snowplow_mobile_context_1) sp
left join unnest (e.com_goeuro_booking_information_context_1) b
WHERE 
    DATE(derived_tstamp) >= "2022-11-30"   
    AND w.experiment_id in ('dreamers-v4','dreamers-android-v1')
    AND e.platform = 'app' -- app test 
),
dreamers_agg as 
(
select experiment_id,
test_assignment,
app_adjust_id,
client_id,
os_family,
min(der

# Result set loaded from BigQuery job as a DataFrame
Query results are referenced from the Job ID ran from BigQuery and the query
does not need to be re-run to explore results. The ```to_dataframe```
[method](https://googleapis.dev/python/bigquery/latest/generated/google.cloud.bigquery.job.QueryJob.html#google.cloud.bigquery.job.QueryJob.to_dataframe)
downloads the results to a Pandas DataFrame by using the BigQuery Storage API.

To edit query syntax, you can do so from the BigQuery SQL editor or in the
```Optional:``` sections below.

In [ ]:
# Running this code will read results from your previous job

job = client.get_job('bquxjob_341e6c0c_185cd6db6c2') # Job ID inserted based on the query results selected to explore
results = job.to_dataframe()
results

experiment_id test_assignment  \
0                dreamers-v4            Test   
1                dreamers-v4            Test   
2                dreamers-v4         Control   
3                dreamers-v4         Control   
4                dreamers-v4         Control   
...                      ...             ...   
1955232  dreamers-android-v1         Control   
1955233  dreamers-android-v1         Control   
1955234  dreamers-android-v1         Control   
1955235          dreamers-v4            Test   
1955236          dreamers-v4            Test   

                            app_adjust_id  \
0        38f33b20bc31774435f6e05dec98c945   
1        f58317d477e755cbf60331c90969f01c   
2        f728554e7ad66c52ce2b83be3271f510   
3        fe0e2630ae3eac8a37d88354bdfe90a6   
4        bd54a1ce11ee26fea6b43c4d89098281   
...                                   ...   
1955232                              None   
1955233  eb8acba251b5cee259aeb26b7187f5bc   
1955234                              None   
1955235  9968f32ffa23b16b2de54df71841d7a1   
1955236  9968f32ffa23b16b2de54df71841d7a1   

                                   client_id os_family  \
0        FEE89364EADA456295794A8AF7429BCD-v2       iOS   
1        1D1310757881452E9044C10F0F9B0135-v2       iOS   
2        E032ADBA75764D83A0914D88D04C6F31-v2       iOS   
3        78C1F456AA704CEAA3B27C911FB73F66-v2       iOS   
4        17EE4BAA80A146A6936D39E40A413946-v2       iOS   
...                                      ...       ...   
1955232  e82028b4e54343a790b26c5f4fb91f5e-v2   Android   
1955233  e82028b4e54343a790b26c5f4fb91f5e-v2   Android   
1955234  e82028b4e54343a790b26c5f4fb91f5e-v2   Android   
1955235  ABCA6BD8C01A41E689B90F206EB0AF32-v2       iOS   
1955236  ABCA6BD8C01A41E689B90F206EB0AF32-v2       iOS   

                          first_instance  num_bookings  \
0       2022-12-06 21:44:08.911000+00:00             0   
1       2023-01-13 16:54:57.125000+00:00             0   
2       2023-01-06 11:07:52.021000+00:00             0   
3       2023-01-18 22:42:59.871000+00:00             0   
4       2022-12-05 13:32:07.834000+00:00             0   
...                                  ...           ...   
1955232 2023-01-19 23:39:35.955000+00:00             0   
1955233 2023-01-19 22:25:03.597000+00:00             0   
1955234 2023-01-19 23:39:35.955000+00:00             0   
1955235 2023-01-04 21:00:10.790000+00:00             0   
1955236 2023-01-04 21:00:10.790000+00:00             0   

                                 search_id                 search_ts  \
0        L026E8A310FA249268BBE5EEBB879CD4B 2022-12-01 21:59:45+00:00   
1        EB9D1E46B62394ABFAE08CB521D44CDB7 2022-12-01 12:19:43+00:00   
2        E7AEBB8BE3449470AA716D9E5288476D9 2022-12-01 18:35:49+00:00   
3        L6DA74641409B4C10930FF14F797081EC 2022-12-01 13:06:54+00:00   
4        L96DF389234BD4994866A0210161902D2 2022-12-01 15:30:40+00:00   
...                                    ...                       ...   
1955232  E57FC05092AD24977B06AD519E04131A8 2023-01-12 22:20:06+00:00   
1955233  E63275EC2CEC74E57BAD3E8AA4B775E07 2023-01-12 22:18:25+00:00   
1955234  E63275EC2CEC74E57BAD3E8AA4B775E07 2023-01-12 22:18:25+00:00   
1955235  EF20832800C4B4DDAAD8DC2EDDB0C47BB 2023-01-12 22:51:37+00:00   
1955236  EEEBFBF98532B4E7CB723E1A4E8E28AB3 2023-01-12 21:17:24+00:00   

        search_departure_city_name search_departure_country_name  \
0                       Gothenburg                        Sweden   
1                        Stockholm                        Sweden   
2                        Stockholm                        Sweden   
3                           Prague                Czech Republic   
4                             Luqa                         Malta   
...                            ...                           ...   
1955232                  Amsterdam                   Netherlands   
1955233                  Amsterdam                   Netherlands   
1955234                  A

In [ ]:
mapping_destinations_to_eng={'Afragola':'Afragola',
 'Ancona':"Ancona",
 'Arezzo':"Arezzo",
 'Avellino':'Avellino',
 'Bari':'Bari',
 'Benevent':'Benevento',
 'Benevento':'Benevento',
 'Bergame':'Bergamo',
 'Bergamo':'Bergamo',
 'Bologna':'Bologna',
 'Bolonia':'Bologna',
 'Bolzano':'Bolzano',
 'Bérgamo':'Bergamo',
 'B��rgamo':'Bergamo',
 'Caserta':'Caserta',
 'Como':'Como',
 'Desenzano del Garda':'Desenzano del Garda',
 'Firenze':'Florence',
 'Florence':'Florence',
 'Florencia':'Florence',
 'Florenz':'Florence',
 'Foggia':'Foggia',
 'Genoa':'Genoa',
 'Genova':"Genoa",
 'Génova':'Genoa',
 'Imola':"Imola",
 'La Spezia':'La Spezia',
 'Lecce':'Lecce',
 'Mailand':'Milan',
 'Milan':"Milan",
 'Milano':'Milan',
 'Milán':'Milan',
 'Modena':'Modena',
 'Módena':'Modena',
 'Naples':'Naples',
 'Napoli':'Naples',
 'Nápoles':'Naples',
 'Padova':'Padua',
 'Padua':'Padua',
 'Parigi':'Paris',
 'Paris':'Paris',
 'Parma':'Parma',
 'Parme':'Parma',
 'París':'Paris',
 'Pavia':'Pavia',
 'Pavía':'Pavia',
 'Perugia':'Perugia',
 'Pescara':'Pescara',
 'Peschiera del Garda':'Peschiera del Garda',
 'Piacenza':'Piacenza',
 'Pisa':'Pisa',
 'Plaisance':'Piacenza',
 'Plasencia':'Piacenza',
 'Prato':'Prato',
 'Reggio Emilia':'Reggio Emilia',
 'Riccione':'Riccione',
 'Rimini':'Rimini',
 'Rom':'Rome',
 'Roma':'Rome',
 'Rome':'Rome',
 'Rímini':'Rímini',
 'Salerno':'Salerno',
 'San Severo':'San Severo',
 'Scandicci':'Scandicci',
 'Siena':'Siena',
 'Taranto':'Taranto',
 'Tarento':'Taranto',
 'Torino':'Turin',
 'Trento':'Taranto',
 'Turin':'Turin',
 'Turín':'Turin',
 'Venecia':'Venice',
 'Venedig':'Venice',
 'Venezia':'Venice',
 'Venice':'Venice',
 'Venise':'Venice',
 'Verona':'Verona',
 'Vicenza':'Vicenza',
 'Vérone':'Verona',
 'Zurich':'Zurich',
 'Zurigo':'Zurich',
 'Zúrich':'Zurich'}

In [ ]:
dreamers_mvp=pd.read_csv('Dreamers_MVP.csv',skiprows=8)
destinations_in_dreamers=dreamers_mvp[dreamers_mvp['Country, EN'].isin(["Italy","IT"])].iloc[:,0]
destinations_in_dreamers

0                Afragola
1                  Ancona
2                  Arezzo
3                Avellino
4                    Bari
5               Benevento
6                 Bergamo
7                 Bologna
8                 Bolzano
9                 Caserta
10                   Como
11    Desenzano del Garda
12               Florence
13                 Foggia
14                  Genoa
15                  Imola
16              La Spezia
17                  Lecce
18                  Milan
19                 Modena
20                 Naples
21                  Padua
23                  Parma
24                  Pavia
25                Perugia
26                Pescara
27    Peschiera del Garda
28               Piacenza
29                   Pisa
30                  Prato
31          Reggio Emilia
32               Riccione
33                 Rimini
34                   Rome
35                Salerno
36             San Severo
37              Scandicci
38                  Siena
39          

In [ ]:
engagement=pd.read_csv('engagement.csv')
engagement

experiment_id os_family test_assignment        event_name  \
0              dreamers-v4       iOS            Test     exp-tab_shown   
1              dreamers-v4       iOS            Test     exp-tab_shown   
2              dreamers-v4       iOS            Test     exp-tab_shown   
3              dreamers-v4       iOS            Test     exp-tab_shown   
4              dreamers-v4       iOS            Test  exp-banner_shown   
...                    ...       ...             ...               ...   
18788  dreamers-android-v1   Android            Test     exp-tab_shown   
18789  dreamers-android-v1   Android            Test     exp-tab_shown   
18790  dreamers-android-v1   Android            Test     exp-tab_shown   
18791  dreamers-android-v1   Android            Test     exp-tab_shown   
18792  dreamers-android-v1   Android            Test     exp-tab_shown   

                     collector_tstamp name_tracker  \
0      2022-12-16 21:47:43.621000 UTC         itly   
1      2022-12-16 23:43:01.382000 UTC         itly   
2      2022-12-19 07:28:23.781000 UTC         itly   
3      2022-12-19 08:06:31.849000 UTC         itly   
4      2022-12-18 23:18:51.409000 UTC         itly   
...                               ...          ...   
18788  2023-01-04 11:40:22.303000 UTC         itly   
18789  2023-01-15 22:21:50.392000 UTC         itly   
18790  2022-12-15 20:34:06.563000 UTC         itly   
18791  2022-12-18 08:45:00.673000 UTC         itly   
18792  2023-01-01 17:44:54.041000 UTC         itly   

                                 client_id  
0      0002E187C1B147D8A561AF7FBBC29B1C-v2  
1      0002E187C1B147D8A561AF7FBBC29B1C-v2  
2      0002E187C1B147D8A561AF7FBBC29B1C-v2  
3      0002E187C1B147D8A561AF7FBBC29B1C-v2  
4      0006EBAFE14E4B28B60EB6E4CB497B3A-v2  
...                                    ...  
18788  ff22f4b18c7a4673b29874d9fea6b4ea-v2  
18789  ff2edbe7bd594097b73adfa5eff89b42-v2  
18790  ff3e709d7c994ac685e3410da0903539-v2  
18791  ffc937347f414a0dac7d2defd4ea07da-v2  
18792  ffef0eb689ef436293b9409b7216e609-v2  

[18793 rows x 7 columns]

In [ ]:
destinations_clicked=pd.read_csv('exp_dest_clicked.csv')
destinations_clicked['destination_position_name']=destinations_clicked['destination_position_name'].map(mapping_destinations_to_eng)
destinations_clicked=destinations_clicked[destinations_clicked['destination_position_name'].isin(destinations_in_dreamers)]
destinations_clicked

experiment_id os_family test_assignment      event_name  \
0      dreamers-v4       iOS            Test  exp-dest_shown   
1      dreamers-v4       iOS            Test  exp-dest_shown   
2      dreamers-v4   Unknown            Test  exp-dest_shown   
3      dreamers-v4       iOS            Test  exp-dest_shown   
5      dreamers-v4       iOS            Test  exp-dest_shown   
...            ...       ...             ...             ...   
1840   dreamers-v4       iOS            Test  exp-dest_shown   
1841   dreamers-v4       iOS            Test  exp-dest_shown   
1842   dreamers-v4       iOS            Test  exp-dest_shown   
1843   dreamers-v4       iOS            Test  exp-dest_shown   
1844   dreamers-v4       iOS            Test  exp-dest_shown   

                    collector_tstamp name_tracker  \
0     2022-11-30 13:04:38.283000 UTC         itly   
1     2022-11-30 20:19:04.921000 UTC         itly   
2     2022-11-30 23:04:32.280000 UTC         itly   
3     2022-12-01 07:13:00.989000 UTC         itly   
5     2022-12-01 09:08:33.579000 UTC         itly   
...                              ...          ...   
1840  2023-01-19 00:22:22.731000 UTC         itly   
1841  2023-01-19 00:29:17.905000 UTC         itly   
1842  2023-01-19 00:29:57.457000 UTC         itly   
1843  2023-01-20 00:28:30.714000 UTC         itly   
1844  2023-01-20 00:29:52.191000 UTC         itly   

                                client_id destination_position_name  \
0     6D26B06CB1BA42348A77DD165A8E643D-v2                    Venice   
1     81AF15980E6E4946AB35256D67B2B91C-v2                     Milan   
2     88D9300641C548DEB86AA2967E3B37B3-v2                    Venice   
3     0EF75783A1744825AE3C9C9A063FC387-v2                  Florence   
5     E450CB6FCA0543CCA4D3B0A4DAF24CBC-v2                    Verona   
...                                   ...                       ...   
1840  56F22F597A4043B387834AFDE277CCA1-v2                   Caserta   
1841  56F22F597A4043B387834AFDE277CCA1-v2                 Benevento   
1842  56F22F597A4043B387834AFDE277CCA1-v2                 La Spezia   
1843  04320E7DC27048D2B7ABC48478DE14FA-v2                      Bari   
1844  04320E7DC27048D2B7ABC48478DE14FA-v2                 La Spezia   

     default_origin_position_name selected_origin_position_name  
0                          Verona                        Verona  
1                         Bergamo                       Bergamo  
2                           Milan                         Milan  
3                            Rome                          Rome  
5                        Florence                      Florence  
...                           ...                           ...  
1840                         Rome                          Rome  
1841                         Rome                          Rome  
1842                         Rome                          Rome  
1843                      Bologna                       Bologna  
1844                      Bologna                       Bologna  

[1516 rows x 10 columns]

In [ ]:
results.groupby(['experiment_id','test_assignment']).agg({"client_id":"nunique"})


client_id
experiment_id       test_assignment           
dreamers-android-v1 Control              19559
                    Test                 19509
dreamers-v4         Control              27531
                    Test                 27089

In [ ]:
engagement.groupby(['os_family','event_name']).agg({"client_id":"nunique"})

client_id
os_family event_name                 
Android   exp-tab_shown          2270
Unknown   exp-banner_shown         90
          exp-tab_shown            29
iOS       exp-banner_shown       5716
          exp-tab_shown          3192

In [ ]:
temp1 =destinations_clicked.groupby(['os_family','destination_position_name']).agg({"client_id":"nunique"}).reset_index()
print(len(temp1[temp1['destination_position_name'].isin(list(destinations_in_dreamers))]))
temp1.columns=['OS','Destination','Number of Clients visting']
temp1=temp1[temp1['OS'].isin(['Android','iOS'])]

92


In [ ]:
temp2=temp1.pivot(index=['Destination'],columns=['OS'],values=['Number of Clients visting']).reset_index()
temp2.columns=['Destination',"Android","IOS"]
temp2=temp2.fillna(0)
temp2['TOTAL']=temp2['Android']+temp2['IOS']
temp2['Normalized Android']=round(temp2['Android']*100/sum(temp2['Android']),2)
temp2['Normalized IOS']=round(temp2['IOS']*100/sum(temp2['IOS']),2)
temp2['Normalized TOTAL']=round(temp2['TOTAL']*100/sum(temp2['TOTAL']),2)
temp2=temp2.sort_values(['Normalized TOTAL'],ascending=False)
temp2.to_csv('Destination_wise_Interactions.csv',index=False)


In [ ]:
# destinations_clicked.groupby(['os_family','client_id']).agg({"destination_position_name":["nunique","unique"],
#                                                              "collector_tstamp":['min','max']}).reset_index().to_csv('User_interactions.csv',index=False)

In [ ]:
temp3=destinations_clicked.groupby(['os_family','client_id']).agg({"destination_position_name":["nunique","unique"],
                                                              "collector_tstamp":['min','max']}).reset_index()

In [ ]:
temp4=destinations_clicked.groupby(['os_family','client_id','destination_position_name']).agg({"collector_tstamp":['min','max','nunique']}).reset_index()
temp4.columns=['os','client_id','destination_position_name','first_visit','last_visit',"num_visits"]
temp4.first_visit=pd.to_datetime(temp4.first_visit)
temp4.last_visit=pd.to_datetime(temp4.last_visit)
temp4

os                            client_id destination_position_name  \
0     Android  00acee0f676549c8b17dcb558e6da49e-v2                    Naples   
1     Android  00b82ce484ac40e699c9f58ab561983d-v2                  Florence   
2     Android  00f644c65766442a85f1952318dda06d-v2                   Taranto   
3     Android  011dd5f0e514438fa5167d1839d29fa6-v2                   Salerno   
4     Android  01d43d646517422d8c6d918f243880d0-v2                      Bari   
...       ...                                  ...                       ...   
1362      iOS  FDBFDCBCFB01460185CD82B71041867B-v2                     Pavia   
1363      iOS  FDBFDCBCFB01460185CD82B71041867B-v2                  Piacenza   
1364      iOS  FE52A30CC92E4FC6A218C1528FD5D0E0-v2                   Bologna   
1365      iOS  FE52A30CC92E4FC6A218C1528FD5D0E0-v2                    Venice   
1366      iOS  FE5C2342AC0A4F86A64A51C5CF034BB4-v2                    Naples   

                          first_visit                       last_visit  \
0    2022-12-03 09:44:00.650000+00:00 2022-12-03 09:44:00.650000+00:00   
1    2022-12-25 00:24:52.480000+00:00 2022-12-25 00:24:52.480000+00:00   
2    2023-01-01 00:18:19.310000+00:00 2023-01-01 00:18:19.310000+00:00   
3    2022-12-26 19:17:06.547000+00:00 2022-12-26 19:17:06.547000+00:00   
4    2023-01-08 16:22:32.313000+00:00 2023-01-08 16:22:32.313000+00:00   
...                               ...                              ...   
1362 2023-01-10 21:21:49.443000+00:00 2023-01-10 21:21:49.443000+00:00   
1363 2023-01-10 21:21:23.540000+00:00 2023-01-10 21:21:23.540000+00:00   
1364 2023-01-12 12:04:17.192000+00:00 2023-01-12 12:04:17.192000+00:00   
1365 2022-12-19 12:28:45.210000+00:00 2022-12-19 12:28:45.210000+00:00   
1366 2022-12-18 14:05:40.744000+00:00 2022-12-18 14:05:40.744000+00:00   

      num_visits  
0              1  
1              1  
2              1  
3              1  
4              1  
...          ...  
1362           1  
1363           1  
1364           1  
1365           1  
1366           1  

[1367 rows x 6 columns]

In [ ]:
len(destinations_clicked)

1516

In [ ]:
destinations_clicked.groupby(['os_family']).agg({'client_id':['nunique']})

client_id
            nunique
os_family          
Android         399
Unknown           4
iOS             390

{'Afragola',
 'Ancona',
 'Arezzo',
 'Avellino',
 'Bari',
 'Benevento',
 'Bergamo',
 'Bologna',
 'Bolzano',
 'Caserta',
 'Como',
 'Desenzano del Garda',
 'Florence',
 'Foggia',
 'Genoa',
 'Imola',
 'La Spezia',
 'Lecce',
 'Milan',
 'Modena',
 'Naples',
 'Padua',
 'Parma',
 'Pavia',
 'Perugia',
 'Pescara',
 'Peschiera del Garda',
 'Piacenza',
 'Pisa',
 'Prato',
 'Reggio Emilia',
 'Riccione',
 'Rimini',
 'Rome',
 'Salerno',
 'San Severo',
 'Scandicci',
 'Siena',
 'Taranto',
 'Trento',
 'Turin',
 'Venice',
 'Verona',
 'Vicenza'}

In [ ]:
print("No. of instances in search:",len(results))
searches_test_group=results[(results['test_assignment']=="Test")]

print("No. of instances in test bucket:",len(searches_test_group))
searches_test_group=searches_test_group[searches_test_group['search_arrival_city_name'].isin( list(destinations_in_dreamers) )]

print("No. of instances having same search destinations as recommended by Explorer Tab:",len(searches_test_group))
print ("Unique search destinations:",searches_test_group['search_arrival_city_name'].nunique())

searches_test_group=searches_test_group[searches_test_group['client_id'].isin( list(destinations_clicked['client_id']) )]
print("No. of instances for clients who explored the explorer tab:",len(searches_test_group))

searches_test_group["search_rank"] = searches_test_group.groupby(["client_id","search_arrival_city_name"])["search_ts"].rank(method="dense")
searches_test_group=searches_test_group.sort_values(['client_id','search_arrival_city_name','search_rank'])


No. of instances in search: 1955237
No. of instances in test bucket: 969770
No. of instances having same search destinations as recommended by Explorer Tab: 406668
Unique search destinations: 43
No. of instances for clients who explored the explorer tab: 10749


In [ ]:
# matched_search_data=(searches_test_group[searches_test_group['client_id'].isin(destinations_clicked['client_id'])])
# unmatched_search_data=(searches_test_group[~searches_test_group['client_id'].isin(destinations_clicked['client_id'])])

In [ ]:
searches_test_group['client_id'].nunique()

584

In [ ]:
temp5=searches_test_group.groupby(['os_family','client_id','search_arrival_city_name']).agg({"search_ts":['min','max','nunique']}).reset_index()
temp5.columns=['os_in_search','client_id','destination_position_name','first_search','last_search','num_searches']
m1=pd.merge(temp4,temp5,how="left")
m1['search_after_exploring_dreamers']=list(map(int,m1['first_visit']<m1['first_search']))
m1

os                            client_id destination_position_name  \
0     Android  00acee0f676549c8b17dcb558e6da49e-v2                    Naples   
1     Android  00b82ce484ac40e699c9f58ab561983d-v2                  Florence   
2     Android  00f644c65766442a85f1952318dda06d-v2                   Taranto   
3     Android  011dd5f0e514438fa5167d1839d29fa6-v2                   Salerno   
4     Android  01d43d646517422d8c6d918f243880d0-v2                      Bari   
...       ...                                  ...                       ...   
1362      iOS  FDBFDCBCFB01460185CD82B71041867B-v2                     Pavia   
1363      iOS  FDBFDCBCFB01460185CD82B71041867B-v2                  Piacenza   
1364      iOS  FE52A30CC92E4FC6A218C1528FD5D0E0-v2                   Bologna   
1365      iOS  FE52A30CC92E4FC6A218C1528FD5D0E0-v2                    Venice   
1366      iOS  FE5C2342AC0A4F86A64A51C5CF034BB4-v2                    Naples   

                          first_visit                       last_visit  \
0    2022-12-03 09:44:00.650000+00:00 2022-12-03 09:44:00.650000+00:00   
1    2022-12-25 00:24:52.480000+00:00 2022-12-25 00:24:52.480000+00:00   
2    2023-01-01 00:18:19.310000+00:00 2023-01-01 00:18:19.310000+00:00   
3    2022-12-26 19:17:06.547000+00:00 2022-12-26 19:17:06.547000+00:00   
4    2023-01-08 16:22:32.313000+00:00 2023-01-08 16:22:32.313000+00:00   
...                               ...                              ...   
1362 2023-01-10 21:21:49.443000+00:00 2023-01-10 21:21:49.443000+00:00   
1363 2023-01-10 21:21:23.540000+00:00 2023-01-10 21:21:23.540000+00:00   
1364 2023-01-12 12:04:17.192000+00:00 2023-01-12 12:04:17.192000+00:00   
1365 2022-12-19 12:28:45.210000+00:00 2022-12-19 12:28:45.210000+00:00   
1366 2022-12-18 14:05:40.744000+00:00 2022-12-18 14:05:40.744000+00:00   

      num_visits os_in_search              first_search  \
0              1      Android 2022-12-03 09:45:03+00:00   
1              1      Android 2022-12-03 11:45:34+00:00   
2              1          NaN                       NaT   
3              1          NaN                       NaT   
4              1          NaN                       NaT   
...          ...          ...                       ...   
1362           1          iOS 2023-01-10 21:22:05+00:00   
1363           1          NaN                       NaT   
1364           1          iOS 2023-01-15 20:40:09+00:00   
1365           1          NaN                       NaT   
1366           1          iOS 2022-12-18 14:06:11+00:00   

                   last_search  num_searches  search_after_exploring_dreamers  
0    2023-01-01 07:04:12+00:00           2.0                                1  
1    2023-01-11 22:26:08+00:00          11.0                                0  
2                          NaT           NaN                                0  
3                          NaT           NaN                                0  
4                          NaT           NaN                                0  
...                        ...           ...                              ...  
1362 2023-01-10 21:22:05+00:00           1.0                                1  
1363                       NaT           NaN                                0  
1364 2023-01-15 20:40:09+00:00           1.0                                1  
1365                       NaT           NaN                                0  
1366 2022-12-18 14:06:11+00:00           1.0                                1  

[1367 rows x 11 columns]

In [ ]:
temp6=m1.groupby(['destination_position_name','search_after_exploring_dreamers']).agg({"client_id":['nunique']}).reset_index().pivot(index=['destination_position_name'],columns=['search_after_exploring_dreamers']).reset_index()
temp6=temp6.fillna(0)
temp6.columns=['destination','clients_not_searching_after_visiting_explore_tab','clients_searching_after_visiting_explore_tab']

temp6['total']=temp6['clients_not_searching_after_visiting_explore_tab']+temp6['clients_searching_after_visiting_explore_tab']
temp6['conversion_as_search']=round(temp6['clients_searching_after_visiting_explore_tab']*100/temp6['total'],2)
temp6

destination  clients_not_searching_after_visiting_explore_tab  \
0              Afragola                                              10.0   
1                Ancona                                              15.0   
2                Arezzo                                               9.0   
3              Avellino                                              11.0   
4                  Bari                                              26.0   
5             Benevento                                              13.0   
6               Bergamo                                              25.0   
7               Bologna                                              25.0   
8               Bolzano                                              20.0   
9               Caserta                                              18.0   
10                 Como                                              33.0   
11  Desenzano del Garda                                              11.0   
12             Florence                                             101.0   
13               Foggia                                              13.0   
14                Genoa                                              34.0   
15                Imola                                              10.0   
16            La Spezia                                              23.0   
17                Lecce                                              16.0   
18                Milan                                              47.0   
19               Modena                                              10.0   
20               Naples                                              53.0   
21                Padua                                              15.0   
22                Parma                                              15.0   
23                Pavia                                              15.0   
24              Perugia                                              13.0   
25              Pescara                                              10.0   
26  Peschiera del Garda                                               7.0   
27             Piacenza                                              12.0   
28                 Pisa                                              25.0   
29                Prato                                               8.0   
30        Reggio Emilia                                               7.0   
31             Riccione                                              16.0   
32               Rimini                                              16.0   
33                 Rome                                              91.0   
34              Salerno                                              18.0   
35           San Severo                                               3.0   
36            Scandicci                                              11.0   
37                Siena                                              17.0   
38              Taranto                                              44.0   
39                Turin                                              42.0   
40               Venice                                              86.0   
41               Verona                                              35.0   
42              Vicenza                                              11.0   

    clients_searching_after_visiting_explore_tab  total  conversion_as_search  
0                                            6.0   16.0                 37.50  
1                                            1.0   16.0                  6.25  
2                                            3.0   12.0                 25.00  
3                                            3.0   14.0                 21.43  
4                                            8.0   34.0                 23.53  
5                                            0.0   13.0                  0.00  
6                                           10.0   35.0        

In [ ]:
temp6.to_csv('Conversion_Search_Destination_level.csv',index=False)

In [ ]:
m1.groupby(['os','search_after_exploring_dreamers']).agg({'client_id':['nunique']})

client_id
                                          nunique
os      search_after_exploring_dreamers          
Android 0                                     325
        1                                     114
Unknown 0                                       3
        1                                       2
iOS     0                                     305
        1                                     130

In [ ]:
325+114

439

In [ ]:
305+130

435

In [ ]:
m1['search_after_exploring_dreamers'].value_counts()

0    1040
1     327
Name: search_after_exploring_dreamers, dtype: int64

In [ ]:
# m1[m1['search_after_exploring_dreamers']==1].to_csv('Clients_Search_post_Exploring.csv',index=False)

In [ ]:
destinations_clicked_in_dreamers=destinations_clicked[destinations_clicked['destination_position_name'].isin(list(destinations_in_dreamers))]

In [ ]:
destinations_clicked

experiment_id os_family test_assignment      event_name  \
0      dreamers-v4       iOS            Test  exp-dest_shown   
1      dreamers-v4       iOS            Test  exp-dest_shown   
2      dreamers-v4   Unknown            Test  exp-dest_shown   
3      dreamers-v4       iOS            Test  exp-dest_shown   
5      dreamers-v4       iOS            Test  exp-dest_shown   
...            ...       ...             ...             ...   
1840   dreamers-v4       iOS            Test  exp-dest_shown   
1841   dreamers-v4       iOS            Test  exp-dest_shown   
1842   dreamers-v4       iOS            Test  exp-dest_shown   
1843   dreamers-v4       iOS            Test  exp-dest_shown   
1844   dreamers-v4       iOS            Test  exp-dest_shown   

                    collector_tstamp name_tracker  \
0     2022-11-30 13:04:38.283000 UTC         itly   
1     2022-11-30 20:19:04.921000 UTC         itly   
2     2022-11-30 23:04:32.280000 UTC         itly   
3     2022-12-01 07:13:00.989000 UTC         itly   
5     2022-12-01 09:08:33.579000 UTC         itly   
...                              ...          ...   
1840  2023-01-19 00:22:22.731000 UTC         itly   
1841  2023-01-19 00:29:17.905000 UTC         itly   
1842  2023-01-19 00:29:57.457000 UTC         itly   
1843  2023-01-20 00:28:30.714000 UTC         itly   
1844  2023-01-20 00:29:52.191000 UTC         itly   

                                client_id destination_position_name  \
0     6D26B06CB1BA42348A77DD165A8E643D-v2                    Venice   
1     81AF15980E6E4946AB35256D67B2B91C-v2                     Milan   
2     88D9300641C548DEB86AA2967E3B37B3-v2                    Venice   
3     0EF75783A1744825AE3C9C9A063FC387-v2                  Florence   
5     E450CB6FCA0543CCA4D3B0A4DAF24CBC-v2                    Verona   
...                                   ...                       ...   
1840  56F22F597A4043B387834AFDE277CCA1-v2                   Caserta   
1841  56F22F597A4043B387834AFDE277CCA1-v2                 Benevento   
1842  56F22F597A4043B387834AFDE277CCA1-v2                 La Spezia   
1843  04320E7DC27048D2B7ABC48478DE14FA-v2                      Bari   
1844  04320E7DC27048D2B7ABC48478DE14FA-v2                 La Spezia   

     default_origin_position_name selected_origin_position_name  
0                          Verona                        Verona  
1                         Bergamo                       Bergamo  
2                           Milan                         Milan  
3                            Rome                          Rome  
5                        Florence                      Florence  
...                           ...                           ...  
1840                         Rome                          Rome  
1841                         Rome                          Rome  
1842                         Rome                          Rome  
1843                      Bologna                       Bologna  
1844                      Bologna                       Bologna  

[1516 rows x 10 columns]

In [ ]:
destinations_clicked_in_dreamers['collector_tstamp']=pd.to_datetime(destinations_clicked_in_dreamers['collector_tstamp'])

<ipython-input-57-a55c4b8b6fb9>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  destinations_clicked_in_dreamers['collector_tstamp']=pd.to_datetime(destinations_clicked_in_dreamers['collector_tstamp'])


In [ ]:
destinations_clicked_in_dreamers['component']='view_in_explore_tab'

<ipython-input-59-a2378c824f9e>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  destinations_clicked_in_dreamers['component']='view_in_explore_tab'


In [ ]:
destinations_clicked_in_dreamers[['os_family','client_id','destination_position_name','collector_tstamp']]

os_family                            client_id destination_position_name  \
5          iOS  E450CB6FCA0543CCA4D3B0A4DAF24CBC-v2                    Verona   
6          iOS  A50785DF88AF413E9A355C306CE2D1B0-v2                     Genoa   
8          iOS  2AFFD74844E346A2BFFDBE818C4FC255-v2                     Turin   
9          iOS  83C233E8B4E446B4B27C9A6B60A9E93B-v2                    Venice   
10         iOS  C737C292475D4AC3BE6181B46F7A286D-v2                    Verona   
...        ...                                  ...                       ...   
1840       iOS  56F22F597A4043B387834AFDE277CCA1-v2                   Caserta   
1841       iOS  56F22F597A4043B387834AFDE277CCA1-v2                 Benevento   
1842       iOS  56F22F597A4043B387834AFDE277CCA1-v2                 La Spezia   
1843       iOS  04320E7DC27048D2B7ABC48478DE14FA-v2                      Bari   
1844       iOS  04320E7DC27048D2B7ABC48478DE14FA-v2                 La Spezia   

                     collector_tstamp  
5    2022-12-01 09:08:33.579000+00:00  
6    2022-12-01 10:59:37.319000+00:00  
8    2022-12-01 16:13:36.493000+00:00  
9    2022-12-01 16:25:26.458000+00:00  
10   2022-12-01 18:10:30.827000+00:00  
...                               ...  
1840 2023-01-19 00:22:22.731000+00:00  
1841 2023-01-19 00:29:17.905000+00:00  
1842 2023-01-19 00:29:57.457000+00:00  
1843 2023-01-20 00:28:30.714000+00:00  
1844 2023-01-20 00:29:52.191000+00:00  

[1069 rows x 4 columns]

In [ ]:
results['destination_in_dreamers']=list(map(int,results['search_arrival_city_name'].isin(destinations_in_dreamers)))

In [ ]:
results

experiment_id test_assignment  \
0                dreamers-v4            Test   
1                dreamers-v4            Test   
2                dreamers-v4         Control   
3                dreamers-v4         Control   
4                dreamers-v4         Control   
...                      ...             ...   
1955232  dreamers-android-v1         Control   
1955233  dreamers-android-v1         Control   
1955234  dreamers-android-v1         Control   
1955235          dreamers-v4            Test   
1955236          dreamers-v4            Test   

                            app_adjust_id  \
0        38f33b20bc31774435f6e05dec98c945   
1        f58317d477e755cbf60331c90969f01c   
2        f728554e7ad66c52ce2b83be3271f510   
3        fe0e2630ae3eac8a37d88354bdfe90a6   
4        bd54a1ce11ee26fea6b43c4d89098281   
...                                   ...   
1955232                              None   
1955233  eb8acba251b5cee259aeb26b7187f5bc   
1955234                              None   
1955235  9968f32ffa23b16b2de54df71841d7a1   
1955236  9968f32ffa23b16b2de54df71841d7a1   

                                   client_id os_family  \
0        FEE89364EADA456295794A8AF7429BCD-v2       iOS   
1        1D1310757881452E9044C10F0F9B0135-v2       iOS   
2        E032ADBA75764D83A0914D88D04C6F31-v2       iOS   
3        78C1F456AA704CEAA3B27C911FB73F66-v2       iOS   
4        17EE4BAA80A146A6936D39E40A413946-v2       iOS   
...                                      ...       ...   
1955232  e82028b4e54343a790b26c5f4fb91f5e-v2   Android   
1955233  e82028b4e54343a790b26c5f4fb91f5e-v2   Android   
1955234  e82028b4e54343a790b26c5f4fb91f5e-v2   Android   
1955235  ABCA6BD8C01A41E689B90F206EB0AF32-v2       iOS   
1955236  ABCA6BD8C01A41E689B90F206EB0AF32-v2       iOS   

                          first_instance  num_bookings  \
0       2022-12-06 21:44:08.911000+00:00             0   
1       2023-01-13 16:54:57.125000+00:00             0   
2       2023-01-06 11:07:52.021000+00:00             0   
3       2023-01-18 22:42:59.871000+00:00             0   
4       2022-12-05 13:32:07.834000+00:00             0   
...                                  ...           ...   
1955232 2023-01-19 23:39:35.955000+00:00             0   
1955233 2023-01-19 22:25:03.597000+00:00             0   
1955234 2023-01-19 23:39:35.955000+00:00             0   
1955235 2023-01-04 21:00:10.790000+00:00             0   
1955236 2023-01-04 21:00:10.790000+00:00             0   

                                 search_id                 search_ts  \
0        L026E8A310FA249268BBE5EEBB879CD4B 2022-12-01 21:59:45+00:00   
1        EB9D1E46B62394ABFAE08CB521D44CDB7 2022-12-01 12:19:43+00:00   
2        E7AEBB8BE3449470AA716D9E5288476D9 2022-12-01 18:35:49+00:00   
3        L6DA74641409B4C10930FF14F797081EC 2022-12-01 13:06:54+00:00   
4        L96DF389234BD4994866A0210161902D2 2022-12-01 15:30:40+00:00   
...                                    ...                       ...   
1955232  E57FC05092AD24977B06AD519E04131A8 2023-01-12 22:20:06+00:00   
1955233  E63275EC2CEC74E57BAD3E8AA4B775E07 2023-01-12 22:18:25+00:00   
1955234  E63275EC2CEC74E57BAD3E8AA4B775E07 2023-01-12 22:18:25+00:00   
1955235  EF20832800C4B4DDAAD8DC2EDDB0C47BB 2023-01-12 22:51:37+00:00   
1955236  EEEBFBF98532B4E7CB723E1A4E8E28AB3 2023-01-12 21:17:24+00:00   

        search_departure_city_name search_departure_country_name  \
0                       Gothenburg                        Sweden   
1                        Stockholm                        Sweden   
2                        Stockholm                        Sweden   
3                           Prague                Czech Republic   
4                             Luqa                         Malta   
...                            ...                           ...   
1955232                  Amsterdam                   Netherlands   
1955233                  Amsterdam                   Netherlands   
1955234                  A

In [ ]:
results.groupby(['experiment_id','test_assignment','destination_in_dreamers']).agg({'client_id':['nunique']}).reset_index()

experiment_id test_assignment destination_in_dreamers client_id
                                                                 nunique
0  dreamers-android-v1         Control                       0     15728
1  dreamers-android-v1         Control                       1     13641
2  dreamers-android-v1            Test                       0     15743
3  dreamers-android-v1            Test                       1     13607
4          dreamers-v4         Control                       0     22171
5          dreamers-v4         Control                       1     19998
6          dreamers-v4            Test                       0     21700
7          dreamers-v4            Test                       1     19816

In [ ]:
results.groupby(["experiment_id","test_assignment"]).agg({'client_id':['nunique'],
                                                          'search_id':['nunique']}).reset_index()

experiment_id test_assignment client_id search_id
                                         nunique   nunique
0  dreamers-android-v1         Control     19559    331297
1  dreamers-android-v1            Test     19509    322280
2          dreamers-v4         Control     27531    495353
3          dreamers-v4            Test     27089    489796

In [ ]:
temp7=results[results['destination_in_dreamers']==1].groupby(["search_arrival_city_name","test_assignment"]).agg({'search_id':['nunique'],
                                                          'order_uuid':['nunique']}).reset_index()

In [ ]:
temp7

search_arrival_city_name test_assignment search_id order_uuid
                                              nunique    nunique
0                  Afragola         Control       434         27
1                  Afragola            Test       628         17
2                    Ancona         Control      1296         40
3                    Ancona            Test      1597         40
4                    Arezzo         Control       889         43
..                      ...             ...       ...        ...
81                   Venice            Test     24369       1291
82                   Verona         Control     10088        455
83                   Verona            Test     10011        506
84                  Vicenza         Control      2227        166
85                  Vicenza            Test      2518        161

[86 rows x 4 columns]

In [ ]:
temp7.columns=['destination','bucket','searches','bookings']

In [ ]:
temp7.pivot(index=['destination'],columns=['bucket'],values=['searches','bookings']).reset_index().to_csv("Search_Bookings_by destinations.csv")

In [ ]:
temp7.pivot(index=['destination'],columns=['bucket'],values=['searches','bookings']).reset_index()

destination searches        bookings      
bucket                       Control   Test  Control  Test
0                  Afragola      434    628       27    17
1                    Ancona     1296   1597       40    40
2                    Arezzo      889   1038       43    49
3                  Avellino      211    205        2     8
4                      Bari    10905  10376      400   380
5                 Benevento      784    747       24    23
6                   Bergamo     4473   4398      252   226
7                   Bologna    20448  19709     1002  1002
8                   Bolzano     3123   3095      134    73
9                   Caserta     1399   1561       40    56
10                     Como     3957   3835      300   295
11      Desenzano del Garda      610    526       34    34
12                 Florence    27465  28058     1868  2013
13                   Foggia     1956   2056       61    64
14                    Imola      166    256       15    18
15                La Spezia     1515   1658       86    82
16                    Lecce     3245   2998       97    97
17                    Milan    67885  66608     3260  3155
18                   Modena     2100   1934      117    80
19                   Naples    29631  28746      984   969
20                    Padua     4855   4894      236   203
21                    Parma     2911   3159      138   148
22                    Pavia     1072    815       68    70
23                  Perugia     1925   1713       62    65
24                  Pescara     2070   1731       75    73
25      Peschiera del Garda      261    314       19    11
26                 Piacenza     1178   1079       62    45
27                     Pisa    10259  10362      580   684
28                    Prato     1158   1141       71    77
29            Reggio Emilia     1547   1537       88    61
30                 Riccione      299    272       14    12
31                   Rimini     1972   1872       96    72
32                     Rome    58890  58984     2837  2925
33                  Salerno     3175   3381      134   144
34               San Severo      645    411       33    26
35                Scandicci       44     62        1     0
36                    Siena     2735   2961      140   129
37                  Taranto     3148   3071      167   136
38                   Trento     1790   2038       61    65
39                    Turin    18133  17800      797   839
40                   Venice    25476  24369     1347  1291
41                   Verona    10088  10011      455   506
42                  Vicenza     2227   2518      166   161